<!-- <center><center><img src="https://raw.githubusercontent.com/makaires77/fioce/master/assets/logo_fioce.png" 
style="height:150px" alt="Logo_Fiocruz"></center></center> -->

<center><center><img src="https://user-images.githubusercontent.com/61051085/81343928-3ce9d500-908c-11ea-9850-0210b4e94ba0.jpg" 
style="height:150px" alt="Logo_Unifor"></center></center>

# Porspectar Oportunidades de Financiamento
### Busca integrada de financiamento por palavras-chave

In [1]:
# import os
# os.listdir('../../../../requirements.txt')

#sudo dpkg -i google-chrome-stable_current_amd64.deb

# !pip install --user -r ../../../../requirements.txt --trusted-host pypi.org --trusted-host pypi.python.org --trusted-host files.pythonhosted.org

# !pip3 install --upgrade pip
# !/usr/local/bin/chromedriver --version
# !curl -s https://chromedriver.storage.googleapis.com/LATEST_RELEASE

## No Terminal:
# sudo apt-get update
# sudo apt-get install libcurl4-openssl-dev

# Depois:
# %pip install pycurl

# sudo apt-get install graphviz graphviz-dev
# %pip install pygraphviz
# %pip install --upgrade notebook jupyterlab ipywidgets
# %pip install webdriver_manager
# %pip install selenium
# %pip install pyqt5

In [3]:
import os.path
from starlette.applications import Starlette
from starlette.responses import PlainTextResponse

app = Starlette(debug=config.DEBUG)

# Obter o diretório raiz do repositório
base_repo_dir = os.path.dirname(os.path.dirname(os.path.abspath(__file__)))  # Supondo script em /seuprojeto/source/domain

# Construir o caminho relativo para o diretório "static"
static_dir = os.path.join(base_repo_dir, "static")

app.mount(config.STATIC_ROUTE, StaticFiles(directory=static_dir), name=config.STATIC_NAME)

NameError: name 'config' is not defined

### <b>Gerar DataFrame Oportunidades por palavras-chave</b>

In [1]:
from pathlib import Path
from getpass import getpass
from datetime import datetime
from IPython.display import clear_output
import pandas as pd, os, re, sys, time, json, subprocess

## Configurar exibição do pandas para melhor visualizar os dados
pd.set_option('display.max_colwidth', None)
pd.set_option('colheader_justify', 'left')
pd.set_option('display.max_rows', 600)

def find_repo_root(path='.', depth=10):
    ''' 
    Busca o arquivo .git e retorna string com a pasta raiz do repositório
    '''
    # Prevent infinite recursion by limiting depth
    if depth < 0:
        return None
    path = Path(path).absolute()
    if (path / '.git').is_dir():
        return path
    return find_repo_root(path.parent, depth-1)

delay = 10

## Definir a pasta de base do repositório local
base_repo_dir = find_repo_root()

## Sempre construir os caminhos usando os.path.join para compatibilidade WxL
folder_utils = os.path.join(base_repo_dir, 'utils')
folder_domain = os.path.join(base_repo_dir, 'source', 'domain')
folder_data_input = os.path.join(base_repo_dir, '_data', 'in_csv')
folder_data_output = os.path.join(base_repo_dir, '_data', 'out_json')

## Adicionar pastas locais ao sys.path para importar pacotes criados localmente
sys.path.append(folder_utils)
sys.path.append(folder_domain)
from scraper_pasteur import PasteurScraper
from environment_setup import EnvironmentSetup
from scraper_sucupira import SucupiraScraper
from scraper_sucupira_edge import SucupiraScraperEdge
from chromedriver_manager import ChromeDriverManager
from lattes_scrapper import JSONFileManager, LattesScraper, HTMLParser, SoupParser, GetQualis, ArticlesCounter, DictToHDF5, attribute_to_be_non_empty

# Cria instância da classe ChromeDriverManager e verifica compatibilidade entre versões do Chrome e Chromedriver
actualizer = ChromeDriverManager()
actualizer.main()

Versões 127 Chrome e 127 Chromedriver estão compatíveis


In [2]:
from funding_finder import FundingFinder
finder = FundingFinder()

palavras_chave = "nanotecnologia OR Alzheimer"
editais = finder.buscar_editais(palavras_chave)

if editais:
    # Faça o que quiser com os editais encontrados
    for edital in editais:
        print(edital) 
else:
    print("Nenhum edital encontrado.")

Erro ao buscar editais na Plataforma Cnpq: name 'editais_encontrados' is not defined
Erro ao buscar editais na Plataforma Finep: 'NoneType' object is not subscriptable
Erro ao buscar editais na CAPES: 404 Client Error: Not Found for url: https://www.gov.br/capes/pt-br/acesso-a-informacao/editais-de-programas
Erro ao buscar editais na CORDIS: 404 Client Error: Not Found for url: https://cordis.europa.eu/api/en/cordis-h2020/v1/fundingOpportunities?q=nanotecnologia+OR+Alzheimer&type=call&pageSize=100&page=1
Erro ao buscar editais na CORDIS: 404 Client Error: Not Found for url: https://cordis.europa.eu/api/en/cordis-h2020/v1/fundingOpportunities?q=nanotecnologia+OR+Alzheimer&type=call&pageSize=100&page=1
Erro ao buscar editais na CORDIS: 404 Client Error: Not Found for url: https://cordis.europa.eu/api/en/cordis-h2020/v1/fundingOpportunities?q=nanotecnologia+OR+Alzheimer&type=call&pageSize=100&page=1
Nenhum edital encontrado.


## <b>Prospectar toda natureza e localização

In [2]:
lista_palavraschave = [
    'cancer',
    'disease',
    'alzheimer',
    'medicamento',
    'imunologia',
    'immunology',
    'innovation',
    'inovação',
    'therapy',
    'terapia',
]

# lista_palavraschave = [
#     'anticorpos',
#     'parasitologia',
#     '"terapias inovadoras"',
#     '"biologia computacional"',
#     '"novos medicamentos"',
#     'cancer',

from funding_finder import FundingFinder
finder = FundingFinder()

try:
    df_geral, falhas = finder.search_funding(lista_palavraschave, filtros=False)

    # Verificar se o DataFrame não está vazio antes de tentar acessar a coluna 'palavras-chave'
    if df_geral.empty:
        print("Nenhum dado foi extraído.")
    else:
        print()
        print(df_geral['palavras-chave'].value_counts())
        data_filepath = os.path.join(folder_data_output, 'df_fomento_geral.csv')
        df_geral.to_csv(data_filepath, index=False)
        print("DataFrame final salvo em:", data_filepath)

finally:
    # Garantir que o logout seja chamado ao final, mesmo se ocorrerem exceções
    finder._logout()

Inserindo credenciais de acesso...
Login negado pela plataforma com a mensagem: Usuário Inativo.
Entrar em contato com administrador da plataforma financiar para reativar o login de usuário
Falha no login. Encerrando a execução.
Nenhum dado foi extraído.


In [4]:
finder.mount_foment_report(df_geral, 'relatorio_fomento_semfiltros')

Relatório montado disponível em c:\Users\marco\ppgcs\source\visualizations\relatorio_fomento_semfiltros_20240816.html


In [5]:
df=df_geral
df_expandido = df.explode('palavras-chave')
pivot_df = df_expandido.pivot_table(index='titulo', columns='palavras-chave', aggfunc='size', fill_value=0)
pivot_df['Total'] = pivot_df.sum(axis=1)
pivot_df.sort_values(by='Total', ascending=False)

palavras-chave                                                                                                                                                                               alzheimer   
titulo                                                                                                                                                                                                   
NIH - Early and Late Stage Clinical Trials for the Spectrum of Alzheimer’s Disease/Alzheimer’s Related Dementias and Age-Related Cognitive Decline (R01)                                     2          \
DKMS - John Hansen Research Grant 2025                                                                                                                                                       0           
A-T Children's Project - Research Grant Program                                                                                                                                              0           
BioMarin - Corporate Funding Grants                                                                                                                                                          0           
NIH - Analytical and Clinical Validation of Biomarkers for Alzheimer’s Disease (AD) and AD-Related Dementias (ADRD) (U01)                                                                    1           
Fulbright - Distinguished Chair at the University of Texas, M.D. Anderson Cancer Center (MD Anderson)                                                                                        0           
NIH - Academic-Industrial Partnerships (AIP) to Translate and Validate In Vivo Imaging Systems (R01)                                                                                         0           
NIH - Novel Mechanism Research on Neuropsychiatric Symptoms (NPS) in Alzheimer's Dementia (R21 & R01)                                                                                        1           
NIH - Research on Current Topics in Alzheimer's Disease and Its Related Dementias (R01/R21)                                                                                                  1           
Hereditay Disease Foundation - Postdoctoral Fellowships and Grants                                                                                                                           0           
NIH - Precision Approaches in Radiation Synthetic Combinations (R21/R01)                                                                                                                     0           
Dioraphte - Research Programme for Skin-related Neglected Tropical Diseases (NTDs) 2024                                                                                                      0           
Diamond Blackfan Anemia Foundation - Research Grants                                                                                                                                         0           
ADDF - Neuroimaging and CSF Biomarker Program 2024                                                                                                                                           1           
ICO-ECF Six-Month Fellowships for Diagnosis and Therapy of Retinoblastoma                                                                                                                    0           
Cystic Fibrosis Foundation - Path to a Cure: Industry Award Program 2024                                                                                                                     0           
NIH - Seamless Early-Stage Clinical Drug Development (Phase 1 to 2a) for Novel therapeutic Agents for the Spectrum of Alzheimer's Disease (AD) and AD-related Dementias (ADRD) (UG3/UH3)     1           
NIH - Development of Innovative Informatics Methods and Algorithms for Cancer Research and Management (R21)                                                       

In [6]:
df_geral

financiadora                                                                                            
0                                                                                  A-T Children's Project  \
1                                                                   American Academy of Dermatology (AAD)   
2                                                                 American Society of Cytopathology (ASC)   
3                                                                         Cancer Research Institute (CRI)   
4                                                                         Cancer Research Institute (CRI)   
5                                                                      Fanconi Anemia Research Fund, Inc.   
6                                                                   Focused Ultrasound Surgery Foundation   
7                                                            International Council of Ophthalmology (ICO)   
8                                                            International Council of Ophthalmology (ICO)   
9                                                                     National Institutes of Health (NIH)   
10                                                                    National Institutes of Health (NIH)   
11                                                                    National Institutes of Health (NIH)   
12                                                                    National Institutes of Health (NIH)   
13                                                                    National Institutes of Health (NIH)   
14                                                                    National Institutes of Health (NIH)   
15                                                                    National Institutes of Health (NIH)   
16                                                                    National Institutes of Health (NIH)   
17                                                                    National Institutes of Health (NIH)   
18                                                                    National Institutes of Health (NIH)   
19                                                                    National Institutes of Health (NIH)   
20                                                                    National Institutes of Health (NIH)   
21                                                                    National Institutes of Health (NIH)   
22                                                                    National Institutes of Health (NIH)   
23                                                                    National Institutes of Health (NIH)   
24                                                                    National Institutes of Health (NIH)   
25                                                                    National Institutes of Health (NIH)   
26                                                                    National Institutes of Health (NIH)   
27                                                                    National Institutes of Health (NIH)   
28                                                                    National Institutes of Health (NIH)   
29                                                                    National Institutes of Health (NIH)   
30                                                                    National Institutes of Health (NIH)   
31                                                                    National Institutes of Health (NIH)   
32                                                                    National Institutes of Health (NIH)   
33                                                                    National Institutes of Health (NIH)   
34                                                                    National Institutes of Health (NIH)   
35                                                                    National I

## <b>Gerar Prospecção com filtro: Pesquisa/Inovação/Ceará</b>

In [7]:
# Chamada à classe e método
from funding_finder import FundingFinder
finder = FundingFinder()
df_ceara, falhas = finder.search_funding(lista_palavraschave, filtros=True)

# Verificar se o DataFrame não está vazio antes de tentar acessar a coluna 'palavras-chave'
if not df_ceara.empty:
    print()
    print(df_ceara['palavras-chave'].value_counts())
    data_filepath = os.path.join(folder_data_output, 'df_fomento_ceara.csv')
    df_ceara.to_csv(data_filepath, index=False)
    print("DataFrame final salvo em:", data_filepath)
else:
    print("Nenhum dado foi extraído.")

Inserindo credenciais de acesso...
Login realizado com sucesso.

Buscando programas de fomento para: cancer, aguarde...


Extraindo oportunidades para: cancer: 100%|██████████| 52/52 [00:25<00:00,  2.04it/s]



Buscando programas de fomento para: disease, aguarde...


Extraindo oportunidades para: disease: 100%|██████████| 99/99 [00:49<00:00,  1.99it/s]



Buscando programas de fomento para: alzheimer, aguarde...


...


Buscando programas de fomento para: therapy, aguarde...


Extraindo oportunidades para: therapy: 100%|██████████| 31/31 [00:14<00:00,  2.08it/s]



Buscando programas de fomento para: terapia, aguarde...


Extraindo oportunidades para: terapia: 100%|██████████| 2/2 [00:00<00:00,  2.29it/s]


Relatório montado disponível em c:\Users\marco\ppgcs\source\visualizations\relatorio_fomento_20240816.html

palavras-chave
disease        99
cancer         52
inovação       40
innovation     37
therapy        31
alzheimer      25
immunology      3
terapia         2
medicamento     1
imunologia      1
Name: count, dtype: int64
DataFrame final salvo em: c:\Users\marco\ppgcs\_data\out_json\df_fomento_ceara.csv


In [8]:
finder.mount_foment_report(df_ceara, 'relatorio_fomento_filtrado_pesquisas_ceara')

Relatório montado disponível em c:\Users\marco\ppgcs\source\visualizations\relatorio_fomento_filtrado_pesquisas_ceara_20240816.html


In [9]:
df=df_ceara
df_expandido = df.explode('palavras-chave')
pivot_df = df_expandido.pivot_table(index='titulo', columns='palavras-chave', aggfunc='size', fill_value=0)
pivot_df['Total'] = pivot_df.sum(axis=1)
pivot_df.sort_values(by='Total', ascending=False)

palavras-chave                                                                                                                                                                               alzheimer   
titulo                                                                                                                                                                                                   
NIH - Early and Late Stage Clinical Trials for the Spectrum of Alzheimer’s Disease/Alzheimer’s Related Dementias and Age-Related Cognitive Decline (R01)                                     2          \
DKMS - John Hansen Research Grant 2025                                                                                                                                                       0           
A-T Children's Project - Research Grant Program                                                                                                                                              0           
NIH - Academic-Industrial Partnerships (AIP) to Translate and Validate In Vivo Imaging Systems (R01)                                                                                         0           
NIH - Analytical and Clinical Validation of Biomarkers for Alzheimer’s Disease (AD) and AD-Related Dementias (ADRD) (U01)                                                                    1           
BioMarin - Corporate Funding Grants                                                                                                                                                          0           
NIH - Systematic Testing of Radionuclides in Preclinical Experiments (STRIPE) (R21/R01)                                                                                                      0           
Focused Ultrasound Surgery Foundation - General Awards Program                                                                                                                               0           
NIH - Understanding Expectancies in Cancer Symptom Management (R01)                                                                                                                          0           
NIH - Alzheimer's Clinical Trials Consortium (ACTC) Clinical Trials (R01)                                                                                                                    1           
NIH - Access and Manipulation of Brain Cell Subtypes Implicated in Aging and AD/ADRD (R61/R33)                                                                                               1           
NIH - Utilizing the PLCO Biospecimens Resource to Bridge Gaps in Cancer Etiology and Early Detection Research (U01)                                                                          1           
International Council of Ophthalmology - ICO-Children's Eye Cancer Foundation Three-Month Retinoblastoma Fellowship                                                                          0           
Hereditay Disease Foundation - Postdoctoral Fellowships and Grants                                                                                                                           0           
Gateway Cancer Research - Grants                                                                                                                                                             0           
Fibrolamellar Cancer Foundation - Research grant program leading to improved understanding and curative treatments for fibrolamellar carcinoma (FLC).                                        0           
NIH - Small Research Grant Program for the Next Generation of Researchers in AD/ADRD Research (R03)                                                                                          1           
Fara - Kyle Bryant Translational Research Award                                                                                                                   

## Gerar embeedings

In [10]:
df.keys()

Index(['financiadora', 'titulo', 'detalhes', 'palavras-chave', 'quantidade'], dtype='object')

In [11]:
import numpy as np
for i in df['detalhes']:
    if i is not np.NaN:
        print(i.get('descricao'))
    else:
        print(None)
    print()

The A-T Children's Project is a non-profit organization that raises funds to support and coordinate biomedical research projects, scientific conferences and a clinical center aimed at finding life-improving therapies and a cure for ataxia-telangiectasia (A-T). A-T is a rare, genetic disease that attacks children, causing progressive loss of muscle control, cancer, and immune system problems.
The Research Grant Program supports promising research with sound scientific rationale. No idea is too novel for us to consider, as long as it has clear relevance for people with ataxia telangiectasia (A-T) and the potential to lead to a therapy. We welcome applications from academia and industry scientists, small biotechnology and large pharmaceutical companies, and even from venture capital firms that are incubating new technologies which may hold promise for A-T. Our portfolio spans basic, translational and clinical research.

The American Society of Cytopathology (ASC), founded in 1951, is a di

In [12]:
import numpy as np
for i in df['detalhes']:
    if i is not np.NaN:
        print(i.get('elegibilidade'))
    else:
        print(None)
    print()

Proposals from young investigators, established principal investigators and clinicians, scientists from other disciplines, and individuals with innovative new ideas for A-T research are encouraged, from academia as well as industry.
Scientists from the US and around the globe are welcome to apply for the funding.
Junior investigators are particularly encouraged to apply for grants, as we are eager to bring new people into the A-T research field who may commit their career and labs to this disease long into the future. We welcome fresh insights.

The Patient Advocacy Grant is open to all members of the ASC, patient advocacy groups and neighboring societies.
Grant awardee(s) will be required to present a progress report of their patient advocacy work in the form of an article for a future edition of The ASC Bulletin.
The grant awardees will be announced at the Annual Scientific Meeting.

Candidates for a CLIP Grant must hold a faculty appointment as a tenure-track assistant professor (or

In [13]:
texto_detalhes = df['detalhes'][3].get('elegibilidade')
texto_detalhes

'Applicants must hold a faculty appointment as a tenure-track assistant professor (or higher rank) at the time of award activation. If not, documentation from their institution must accompany the Letter of Intent indicating they will hold the position of assistant professor (or higher rank) by the time of award activation.'

In [14]:
from funding_embeddings import FundingEmbeddings
embedder = FundingEmbeddings()
embedding = embedder.generate_embedding(texto_detalhes)

print(embedding)

tensor([[-2.3377e-01,  6.2677e-02,  1.6830e-01,  5.8381e-03,  5.6809e-01,
          1.6797e-01,  3.5528e-01, -3.5407e-01, -5.5186e-01,  1.7107e-02,
         -5.2064e-01,  3.5001e-03,  5.5736e-02,  2.4797e-01,  4.5206e-01,
         -2.1835e-01, -1.3520e-01, -5.0688e-01,  2.8198e-01,  6.2697e-01,
         -3.0766e-01, -1.5775e-01,  8.5129e-03,  2.7983e-01,  1.6388e-01,
         -3.0744e-01, -1.8592e-01,  2.3932e-02,  2.5190e-02, -2.7992e-01,
          9.1589e-02,  3.7739e-01, -1.2728e-01,  1.0163e+00, -1.1037e-01,
          3.0684e-01,  5.2245e-02,  1.5949e-02,  2.6377e-01, -1.0775e-01,
          8.6878e-01,  4.9081e-01, -5.0782e-01, -2.8770e-01,  2.8135e-01,
         -5.8536e-01,  2.1259e-01, -2.0592e-01, -4.6290e-01,  5.3200e-01,
         -2.3911e-01, -4.0207e-01,  5.8962e-01,  1.9542e-02,  3.8556e-02,
          1.1760e-01,  9.0623e-02,  3.8387e-01, -2.9763e-01,  1.3387e-01,
          3.2161e-01,  1.3530e-01,  3.8053e-02,  1.2901e-01, -2.1717e-01,
         -8.7840e-02,  8.8154e-01,  3.